In [1]:
%load_ext autoreload
%autoreload 2
import numpy as np
import os
import pickle
from sklearn.model_selection import train_test_split
import xgboost as xgb
from sklearn.metrics import accuracy_score, roc_auc_score
import sys
sys.path.append(os.path.abspath(".."))
import torch
import pandas as pd
from datasets import PressingSequenceDataset, SoccerMapInputDataset
import config as C
import features as F
from bisect import bisect_right

2025-06-14 01:41:07.585409: E tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:9342] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2025-06-14 01:41:07.585466: E tensorflow/compiler/xla/stream_executor/cuda/cuda_fft.cc:609] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2025-06-14 01:41:07.585516: E tensorflow/compiler/xla/stream_executor/cuda/cuda_blas.cc:1518] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-06-14 01:41:07.639422: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2025-06-14 01:41:11.152199: W tensorflow/compiler/

/home/exPress/express-v2


In [14]:
data_path = "/home/exPress/express-v2/data/bepro/pressing_intensity"

with open(f"{data_path}/train_dataset.pkl", "rb") as f:
    train_dataset = pickle.load(f)

# with open(f"{data_path}/valid_dataset.pkl", "rb") as f:
#     valid_dataset = pickle.load(f)


with open(f"{data_path}/test_dataset.pkl", "rb") as f:
    test_dataset = pickle.load(f)

len(train_dataset), len(test_dataset)

(4469, 1130)

In [4]:
print(f"Features : {sample['features'].shape}")
print(f"Pressing Intensity : {sample['pressing_intensity'].shape}")
print(f"Labels : {sample['label']}")
print(f"Presser ID : {sample['presser_id']}")
print(f"Players Order : {sample['agent_order']}")
print(f"match info : {sample['match_info']}")

Features : torch.Size([1, 23, 8])
Pressing Intensity : torch.Size([1, 11, 11])
Labels : 0
Presser ID : 500140
Players Order : ['145703', '188178', '250079', '250101', '369783', '500133', '500135', '500138', '500140', '500142', '62386', '139210', '143410', '161110', '187326', '188267', '286696', '344465', '344466', '344467', '500124', '77579', 'ball']
match info : 126285-2.0-134401


In [28]:
from collections import defaultdict

# game_id → set(frame_id) 매핑
game_to_frames = defaultdict(set)

for idx, sample in enumerate(test_dataset):
    game_id, _, frame_id_str = sample['match_info'].split('-')
    frame_id = int(frame_id_str)
    game_to_frames[game_id].add(frame_id)  # set이라서 중복 자동 제거

# 출력
for gid, frames in game_to_frames.items():
    print(f"Game {gid}: {len(frames)} frame_ids")


Game 126408: 209 frame_ids
Game 126411: 242 frame_ids
Game 126418: 230 frame_ids
Game 126424: 226 frame_ids
Game 126429: 223 frame_ids


In [26]:
len(set(game_ids))

20

In [15]:
from collections import defaultdict
import torch
import pandas as pd
import os

def compute_second_half_offset(tracking_df):

    df = tracking_df.copy()
    df['timestamp'] = pd.to_timedelta(df['timestamp'])

    # 전반 종료 시점
    first_half_end = df[df['period_id'] == 1]['timestamp'].max()

    # 후반 시작 시점
    second_half_start = df[df['period_id'] == 2]['timestamp'].min()

    # offset 계산 (후반 timestamp에 더할 시간)
    offset = (first_half_end - second_half_start).total_seconds()

    return offset

def update_features(dataset, feature_list, processed_data_path):
    print(f"DEBUG: Dataset length (from __len__): {len(dataset)}")
    # dataset.loaded_data는 PressingSequenceDataset 클래스 내부에 있을 변수입니다.
    # 함수 외부에서 접근할 때는 dataset.loaded_data로 접근해야 합니다.
    # 하지만 __getitem__/__setitem__을 통해 간접적으로 접근하는 것이 권장됩니다.

    game_sample_map = defaultdict(list)

    # 1. game_id 기준으로 샘플 인덱스와 frame_id를 모음
    for idx, sample in enumerate(dataset): # dataset.__len__에 의해 결정되는 길이만큼 루프
        game_id, _, frame_id_str = sample['match_info'].split('-')
        frame_id = int(frame_id_str)
        game_sample_map[game_id].append((idx, frame_id))

    # 2. game_id 단위로 모든 처리 (데이터 로드, timestamp 매핑, 피처 계산, 데이터셋 업데이트)
    for game_id, frame_infos_for_game in game_sample_map.items():
        print(f"\n--- Processing Game ID: {game_id} ---")

        # 2-1. 해당 game_id의 데이터 로드 (스코프가 이 루프 내부로 제한됨)
        tracking_df = pd.read_csv(os.path.join(processed_data_path, game_id, f"{game_id}_traces.csv"))
        events_df = pd.read_csv(os.path.join(processed_data_path, game_id, f"{game_id}_merged.csv"))
        teams_df = pd.read_csv(os.path.join(processed_data_path, game_id, f"{game_id}_teams.csv"))
        events_df = events_df.sort_values("timestamp")
        events_df["time_seconds"] = pd.to_numeric(events_df["time_seconds"], errors="coerce")

        offset = compute_second_half_offset(tracking_df)

        # 2-2. frame_id -> timestamp 매핑 (스코프가 이 루프 내부로 제한됨)
        frame_id_to_ts = {}
        for fid in [fid for _, fid in frame_infos_for_game]: # 현재 game_id에 해당하는 fid들만 사용
            row = tracking_df[tracking_df["frame_id"] == fid]
            if not row.empty:
                ts = pd.to_timedelta(row.iloc[0]["timestamp"]).total_seconds()
                if row.iloc[0]["period_id"] == 2:
                    ts += offset
                frame_id_to_ts[fid] = ts

        # 2-3. 피처 계산 및 버퍼링 (현재 game_id에 속하는 샘플들만 처리)
        # 이 버퍼는 현재 game_id 내에서만 사용됩니다.
        current_game_sample_feature_buffer = defaultdict(list) 

        for feature_name in feature_list: # 각 피처 이름에 대해
            func = getattr(F, feature_name)

            # 현재 game_id의 샘플들만 순회
            for sample_idx, fid in frame_infos_for_game: 
                if fid not in frame_id_to_ts:
                    print(f"WARN: Skipping sample_idx {sample_idx}, fid {fid} for game {game_id} as timestamp not found.")
                    continue

                # dataset[sample_idx]는 __getitem__을 통해 데이터를 가져옵니다.
                # __getitem__이 반환하는 딕셔너리는 'features'를 포함해야 합니다.
                # 중요한 점: __getitem__에서 정규화된 텐서를 반환한다면,
                # 새로운 피처는 정규화되지 않은 상태로 추가되므로 추후 문제가 될 수 있습니다.
                # 가장 안전한 방법은 __getitem__이 원본 데이터를 반환하고,
                # 모델 입력 직전에 정규화를 수행하거나, 피처 추가 로직에서 정규화 과정을 포함하는 것입니다.
                
                # 여기서는 __getitem__이 반환하는 현재 상태의 features를 사용합니다.
                current_sample_data_dict = dataset[sample_idx] 
                feature_tensor = current_sample_data_dict['features'] 
                
                # B, N, D는 feature_tensor의 현재 모양에서 가져옵니다.
                B, N, D = feature_tensor.shape
                ts = frame_id_to_ts[fid]

                full_past_events = events_df[events_df["time_seconds"] < ts].sort_values("time_seconds", ascending=False)
                past_events = full_past_events.head(B)

                if past_events.empty:
                    feat_val = np.full((B, 1), np.nan, dtype=np.float32)
                else:
                    if feature_name == "sum_pitch_control":
                        feat_val = func(past_events, teams_df)
                        feat_val = feat_val.iloc[:, 1]
                    elif feature_name in ["time_since_last_opponent_action", "cumul_goal", "goaldiff"]:
                        feat_val = func(past_events, events_df)
                        feat_val = feat_val.iloc[:, 1]
                    else:
                        feat_val = func(past_events)
                   
                    if isinstance(feat_val, pd.DataFrame):
                        feat_val = feat_val.values.astype(np.float32)
                    elif isinstance(feat_val, np.ndarray):
                        feat_val = feat_val.astype(np.float32)
                
                if feat_val.ndim == 1:
                    feat_val = feat_val.reshape(-1, 1) # 항상 (B, 1) 또는 (이벤트 수, 1) 형태로 유지

                new_feature_tensor = torch.tensor(feat_val, dtype=torch.float32).unsqueeze(1).expand(-1, N, -1) # (B, N, F)
                current_game_sample_feature_buffer[sample_idx].append(new_feature_tensor)
                print(f"DEBUG: New feature '{feature_name}' for sample {sample_idx} shape: {new_feature_tensor.shape}", flush=True)

        # 2-4. 현재 game_id에 대한 모든 피처 계산이 끝나면, dataset에 최종적으로 업데이트
        for sample_idx, new_feats_for_sample in current_game_sample_feature_buffer.items():
            # dataset에서 해당 sample_idx의 현재 데이터 딕셔너리를 가져옵니다.
            current_sample_data_dict = dataset[sample_idx] # __getitem__ 호출

            original_feature_tensor = current_sample_data_dict['features'] # 현재 features 텐서

            # 새롭게 추가될 모든 피처 텐서들을 dim=-1을 기준으로 횡으로 합칩니다.
            concat_all_new_features = torch.cat(new_feats_for_sample, dim=-1) 

            # 기존 피처 텐서와 새로 합쳐진 피처 텐서를 다시 dim=-1을 기준으로 합칩니다.
            final_concatenated_feature_tensor = torch.cat([original_feature_tensor, concat_all_new_features], dim=-1)

            # 업데이트된 features 텐서를 딕셔너리에 다시 할당합니다.
            current_sample_data_dict['features'] = final_concatenated_feature_tensor

            # dataset의 __setitem__을 호출하여 데이터셋 내부의 실제 데이터를 업데이트합니다.
            # 이 라인이 실행될 때 __setitem__이 없으면 TypeError가 발생하고,
            # __setitem__이 잘못 구현되면 IndexError가 발생합니다.
            dataset[sample_idx] = current_sample_data_dict 

            print(f"DEBUG: Final shape for sample {sample_idx} in game {game_id}: {dataset[sample_idx]['features'].shape}", flush=True)
            # 이 print는 __getitem__이 호출되어 반환된 값을 보여줍니다.




In [27]:
game_id = '126285'
events_df = pd.read_csv(os.path.join(processed_data_path, game_id, f"{game_id}_merged.csv"))

In [ ]:
game_id = '126285'
events_df = pd.read_csv(os.path.join(processed_data_path, game_id, f"{game_id}_merged.csv"))
teams_df = pd.read_csv(os.path.join(processed_data_path, game_id, f"{game_id}_teams.csv"))
data = sum_pitch_control(events_df, teams_df)

In [74]:
def print_feature_shape_diff(dataset, dataset_name="dataset"):
    print(f"[{dataset_name}] Feature shape before update:")
    for i in range(3):  # 앞의 3개 샘플만 예시로 확인
        print(f"  Sample {i}: {dataset[i]['features'].shape}")

# 1. 업데이트 전
print_feature_shape_diff(train_dataset, "train_dataset (before)")
print_feature_shape_diff(test_dataset, "test_dataset (before)")

[train_dataset (before)] Feature shape before update:
  Sample 0: torch.Size([3, 23, 8])
  Sample 1: torch.Size([4, 23, 8])
  Sample 2: torch.Size([2, 23, 8])
[test_dataset (before)] Feature shape before update:
  Sample 0: torch.Size([2, 23, 8])
  Sample 1: torch.Size([2, 23, 8])
  Sample 2: torch.Size([1, 23, 8])


In [16]:
processed_data_path = "/home/exPress/express-v2/data/bepro/processed"
feature_list = [
                'distance_ball_goal','distance_ball_sideline', 'distance_ball_goalline', 'get_actor_speed', 'angle_to_goal', 'compute_time_elapsed','get_min_defender_distance', 'get_closest_defender_speed',
                'get_speed_diff_actor_defender', 'nb_of_3m_radius', 'nb_of_5m_radius','nb_of_10m_radius',
                'get_dist_defender_to_sideline','get_dist_defender_to_goaline']

update_features(train_dataset, feature_list, processed_data_path)
update_features(test_dataset, feature_list, processed_data_path)

DEBUG: Dataset length (from __len__): 4469

--- Processing Game ID: 126285 ---
DEBUG: New feature 'distance_ball_goal' for sample 0 shape: torch.Size([3, 23, 1])
DEBUG: New feature 'distance_ball_goal' for sample 1 shape: torch.Size([4, 23, 1])
DEBUG: New feature 'distance_ball_goal' for sample 2 shape: torch.Size([2, 23, 1])
DEBUG: New feature 'distance_ball_goal' for sample 3 shape: torch.Size([2, 23, 1])
DEBUG: New feature 'distance_ball_goal' for sample 4 shape: torch.Size([3, 23, 1])
DEBUG: New feature 'distance_ball_goal' for sample 5 shape: torch.Size([2, 23, 1])
DEBUG: New feature 'distance_ball_goal' for sample 6 shape: torch.Size([2, 23, 1])
DEBUG: New feature 'distance_ball_goal' for sample 7 shape: torch.Size([4, 23, 1])
DEBUG: New feature 'distance_ball_goal' for sample 8 shape: torch.Size([3, 23, 1])
DEBUG: New feature 'distance_ball_goal' for sample 9 shape: torch.Size([2, 23, 1])
DEBUG: New feature 'distance_ball_goal' for sample 10 shape: torch.Size([3, 23, 1])
DEBUG: 

In [17]:
print(train_dataset[0]["features"].shape)
print(test_dataset[0]["features"].shape)

torch.Size([3, 23, 23])
torch.Size([2, 23, 23])


In [18]:
num_seq = 150
num_agents = 11
use_pressing_intensity = True
selected_features_idx = [i for i in range(23)]

train_features = []
train_labels = []
for i in range(len(train_dataset)):
    sample = train_dataset[i]
    x_tensor = sample['features'][..., selected_features_idx][-1:]
    press_intensity = sample['pressing_intensity'][-1:]
    y_tensor = sample['label']
    
    # Flatten the sequence data: shape (sequence_length, num_features) -> (sequence_length*num_features,)
    feature_vector = x_tensor.flatten().numpy()
    if use_pressing_intensity:
        if press_intensity.shape[1] != num_agents:
            pad_tensor = torch.zeros(press_intensity.shape[0], num_agents-press_intensity.shape[1], press_intensity.shape[2])
            press_intensity = torch.cat([press_intensity, pad_tensor], dim=1)
            
        if press_intensity.shape[2] != num_agents:
            pad_tensor = torch.zeros(press_intensity.shape[0], press_intensity.shape[1], num_agents-press_intensity.shape[2])
            press_intensity = torch.cat([press_intensity, pad_tensor], dim=2)
        
        press_vector = press_intensity.flatten().numpy()
        # Concatenate the flattened sequence data with the pressing intensity
        feature_vector = np.concatenate((feature_vector, press_vector))
    train_features.append(feature_vector)
    train_labels.append(y_tensor.item())


test_features = []
test_labels = []
for i in range(len(test_dataset)):
    sample = test_dataset[i]
    x_tensor = sample['features'][..., selected_features_idx][-1:]
    press_intensity = sample['pressing_intensity'][-1:]
    y_tensor = sample['label']
    
    # Flatten the sequence data: shape (sequence_length, num_features) -> (sequence_length*num_features,)
    feature_vector = x_tensor.flatten().numpy()
    
    if use_pressing_intensity:
        if press_intensity.shape[1] != num_agents:
            pad_tensor = torch.zeros(press_intensity.shape[0], num_agents-press_intensity.shape[1], press_intensity.shape[2])
            press_intensity = torch.cat([press_intensity, pad_tensor], dim=1)
        if press_intensity.shape[2] != num_agents:
            pad_tensor = torch.zeros(press_intensity.shape[0], press_intensity.shape[1], num_agents-press_intensity.shape[2])
            press_intensity = torch.cat([press_intensity, pad_tensor], dim=2)
        
        press_vector = press_intensity.flatten().numpy()
        # Concatenate the flattened sequence data with the pressing intensity
        feature_vector = np.concatenate((feature_vector, press_vector))
    test_features.append(feature_vector)
    test_labels.append(y_tensor.item())

X_train = np.array(train_features)
y_train = np.array(train_labels)

# Split the data into training and testing sets (80% training, 20% testing)
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=0.2, random_state=42)

X_test = np.array(test_features)
y_test = np.array(test_labels)

In [19]:
x_tensor.shape 

torch.Size([1, 23, 23])

In [20]:
def print_dataset_distribution(y_train, y_val, y_test):
    def _print_split(name, labels):
        total = len(labels)
        unique, counts = np.unique(labels, return_counts=True)
        print(f"{name} Set:")
        print(f"  Total samples: {total}")
        for label, count in zip(unique, counts):
            percent = (count / total) * 100
            print(f"    Label {label}: {count:>5} samples ({percent:5.2f}%)")
        print("-" * 40)

    print("\n📊 Dataset Distribution Summary")
    print("=" * 40)
    _print_split("Train", y_train)
    _print_split("Validation", y_val)
    _print_split("Test", y_test)

print_dataset_distribution(y_train, y_val, y_test)


📊 Dataset Distribution Summary
Train Set:
  Total samples: 3575
    Label 0:  3061 samples (85.62%)
    Label 1:   514 samples (14.38%)
----------------------------------------
Validation Set:
  Total samples: 894
    Label 0:   781 samples (87.36%)
    Label 1:   113 samples (12.64%)
----------------------------------------
Test Set:
  Total samples: 1130
    Label 0:   987 samples (87.35%)
    Label 1:   143 samples (12.65%)
----------------------------------------


In [21]:
# Create XGBoost DMatrix objects for train and test sets
dtrain = xgb.DMatrix(X_train, label=y_train)
dtest = xgb.DMatrix(X_val, label=y_val)

# Set XGBoost training parameters
params = {
    'objective': 'binary:logistic',  # binary classification
    'eval_metric': 'auc',            # evaluation metric: AUC
    'max_depth': 6,                  # maximum depth of trees
    'eta': 0.1,                      # learning rate
    'seed': 42
}

# Specify the watchlist to evaluate performance on training and test sets during training
watchlist = [(dtrain, 'train'), (dtest, 'eval')]
num_rounds = 100

In [22]:
bst = xgb.train(params, dtrain, num_rounds, watchlist, early_stopping_rounds=10)

[0]	train-auc:0.86732	eval-auc:0.78693
[1]	train-auc:0.90572	eval-auc:0.80089
[2]	train-auc:0.92585	eval-auc:0.81176
[3]	train-auc:0.94209	eval-auc:0.81389


/opt/conda/envs/expressv2/lib/python3.11/site-packages/xgboost/core.py:726: FutureWarning: Pass `evals` as keyword args.
  warnings.warn(msg, FutureWarning)


[4]	train-auc:0.95348	eval-auc:0.81393
[5]	train-auc:0.96011	eval-auc:0.81627
[6]	train-auc:0.96361	eval-auc:0.82082
[7]	train-auc:0.96890	eval-auc:0.81955
[8]	train-auc:0.97179	eval-auc:0.81860
[9]	train-auc:0.97550	eval-auc:0.82177
[10]	train-auc:0.97748	eval-auc:0.82742
[11]	train-auc:0.97972	eval-auc:0.82882
[12]	train-auc:0.98020	eval-auc:0.83052
[13]	train-auc:0.98259	eval-auc:0.83193
[14]	train-auc:0.98363	eval-auc:0.83322
[15]	train-auc:0.98518	eval-auc:0.83369
[16]	train-auc:0.98632	eval-auc:0.83296
[17]	train-auc:0.98716	eval-auc:0.83272
[18]	train-auc:0.98862	eval-auc:0.83676
[19]	train-auc:0.98978	eval-auc:0.83782
[20]	train-auc:0.99086	eval-auc:0.83802
[21]	train-auc:0.99184	eval-auc:0.83689
[22]	train-auc:0.99264	eval-auc:0.83741
[23]	train-auc:0.99393	eval-auc:0.83826
[24]	train-auc:0.99435	eval-auc:0.83908
[25]	train-auc:0.99486	eval-auc:0.83707
[26]	train-auc:0.99527	eval-auc:0.83621
[27]	train-auc:0.99543	eval-auc:0.83701
[28]	train-auc:0.99624	eval-auc:0.83624
[29]	t

In [13]:
bst = xgb.train(params, dtrain, num_rounds, watchlist, early_stopping_rounds=10)

[0]	train-auc:0.77079	eval-auc:0.56480
[1]	train-auc:0.81633	eval-auc:0.54961
[2]	train-auc:0.86248	eval-auc:0.54618
[3]	train-auc:0.87842	eval-auc:0.57044
[4]	train-auc:0.90155	eval-auc:0.56982


/opt/conda/envs/expressv2/lib/python3.11/site-packages/xgboost/core.py:726: FutureWarning: Pass `evals` as keyword args.
  warnings.warn(msg, FutureWarning)


[5]	train-auc:0.92935	eval-auc:0.56407
[6]	train-auc:0.94120	eval-auc:0.55748
[7]	train-auc:0.95791	eval-auc:0.55323
[8]	train-auc:0.96185	eval-auc:0.56837
[9]	train-auc:0.96629	eval-auc:0.57125
[10]	train-auc:0.97092	eval-auc:0.56945
[11]	train-auc:0.97616	eval-auc:0.56951
[12]	train-auc:0.97919	eval-auc:0.56178
[13]	train-auc:0.98246	eval-auc:0.57820
[14]	train-auc:0.98524	eval-auc:0.58570
[15]	train-auc:0.98860	eval-auc:0.57941
[16]	train-auc:0.98943	eval-auc:0.58200
[17]	train-auc:0.99112	eval-auc:0.58153
[18]	train-auc:0.99209	eval-auc:0.58372
[19]	train-auc:0.99298	eval-auc:0.58693
[20]	train-auc:0.99396	eval-auc:0.57990
[21]	train-auc:0.99467	eval-auc:0.58441
[22]	train-auc:0.99519	eval-auc:0.58697
[23]	train-auc:0.99575	eval-auc:0.59159
[24]	train-auc:0.99606	eval-auc:0.59224
[25]	train-auc:0.99637	eval-auc:0.60097
[26]	train-auc:0.99710	eval-auc:0.60140
[27]	train-auc:0.99767	eval-auc:0.59650
[28]	train-auc:0.99824	eval-auc:0.59520
[29]	train-auc:0.99846	eval-auc:0.59885
[30]	

In [23]:
# W/O Pressing Intensity
# Get predictions on the test set
y_pred = bst.predict(dtest)
y_pred_label = (y_pred > 0.5).astype(int)

# Calculate and print evaluation metrics
accuracy = accuracy_score(y_val, y_pred_label)
auc = roc_auc_score(y_val, y_pred)

print("Test Accuracy: {:.4f}".format(accuracy))
print("Test AUC: {:.4f}".format(auc))

Test Accuracy: 0.8714
Test AUC: 0.8366


# 1. XGBoost

In [10]:
num_seq = 150
num_agents = 11
use_pressing_intensity = False
selected_features_idx = [1, 2, 4, 7]

train_features = []
train_labels = []
for i in range(len(train_dataset)):
    sample = train_dataset[i]
    x_tensor = sample['features'][..., selected_features_idx][-90:]
    press_intensity = sample['pressing_intensity'][-90:]
    y_tensor = sample['label']
    
    # Flatten the sequence data: shape (sequence_length, num_features) -> (sequence_length*num_features,)
    feature_vector = x_tensor.flatten().numpy()
    if use_pressing_intensity:
        if press_intensity.shape[1] != num_agents:
            pad_tensor = torch.zeros(press_intensity.shape[0], num_agents-press_intensity.shape[1], press_intensity.shape[2])
            press_intensity = torch.cat([press_intensity, pad_tensor], dim=1)
            
        if press_intensity.shape[2] != num_agents:
            pad_tensor = torch.zeros(press_intensity.shape[0], press_intensity.shape[1], num_agents-press_intensity.shape[2])
            press_intensity = torch.cat([press_intensity, pad_tensor], dim=2)
        
        press_vector = press_intensity.flatten().numpy()
        # Concatenate the flattened sequence data with the pressing intensity
        feature_vector = np.concatenate((feature_vector, press_vector))
    train_features.append(feature_vector)
    train_labels.append(y_tensor.item())


test_features = []
test_labels = []
for i in range(len(test_dataset)):
    sample = test_dataset[i]
    x_tensor = sample['features'][..., selected_features_idx][-90:]
    press_intensity = sample['pressing_intensity'][-90:]
    y_tensor = sample['label']
    
    # Flatten the sequence data: shape (sequence_length, num_features) -> (sequence_length*num_features,)
    feature_vector = x_tensor.flatten().numpy()
    
    if use_pressing_intensity:
        if press_intensity.shape[1] != num_agents:
            pad_tensor = torch.zeros(press_intensity.shape[0], num_agents-press_intensity.shape[1], press_intensity.shape[2])
            press_intensity = torch.cat([press_intensity, pad_tensor], dim=1)
        if press_intensity.shape[2] != num_agents:
            pad_tensor = torch.zeros(press_intensity.shape[0], press_intensity.shape[1], num_agents-press_intensity.shape[2])
            press_intensity = torch.cat([press_intensity, pad_tensor], dim=2)
        
        press_vector = press_intensity.flatten().numpy()
        # Concatenate the flattened sequence data with the pressing intensity
        feature_vector = np.concatenate((feature_vector, press_vector))
    test_features.append(feature_vector)
    test_labels.append(y_tensor.item())

X_train = np.array(train_features)
y_train = np.array(train_labels)

# Split the data into training and testing sets (80% training, 20% testing)
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=0.2, random_state=42)

X_test = np.array(test_features)
y_test = np.array(test_labels)

In [12]:
def print_dataset_distribution(y_train, y_val, y_test):
    def _print_split(name, labels):
        total = len(labels)
        unique, counts = np.unique(labels, return_counts=True)
        print(f"{name} Set:")
        print(f"  Total samples: {total}")
        for label, count in zip(unique, counts):
            percent = (count / total) * 100
            print(f"    Label {label}: {count:>5} samples ({percent:5.2f}%)")
        print("-" * 40)

    print("\n📊 Dataset Distribution Summary")
    print("=" * 40)
    _print_split("Train", y_train)
    _print_split("Validation", y_val)
    _print_split("Test", y_test)

print_dataset_distribution(y_train, y_val, y_test)


📊 Dataset Distribution Summary
Train Set:
  Total samples: 11392
    Label 0:  9138 samples (80.21%)
    Label 1:  2254 samples (19.79%)
----------------------------------------
Validation Set:
  Total samples: 2849
    Label 0:  2281 samples (80.06%)
    Label 1:   568 samples (19.94%)
----------------------------------------
Test Set:
  Total samples: 1721
    Label 0:  1358 samples (78.91%)
    Label 1:   363 samples (21.09%)
----------------------------------------


In [9]:
# Create XGBoost DMatrix objects for train and test sets
dtrain = xgb.DMatrix(X_train, label=y_train)
dtest = xgb.DMatrix(X_val, label=y_val)

# Set XGBoost training parameters
params = {
    'objective': 'binary:logistic',  # binary classification
    'eval_metric': 'auc',            # evaluation metric: AUC
    'max_depth': 6,                  # maximum depth of trees
    'eta': 0.1,                      # learning rate
    'seed': 42
}

# Specify the watchlist to evaluate performance on training and test sets during training
watchlist = [(dtrain, 'train'), (dtest, 'eval')]
num_rounds = 100

In [10]:
# Train XGBoost model with early stopping on the evaluation set
bst = xgb.train(params, dtrain, num_rounds, watchlist, early_stopping_rounds=10)

/home/work/miniconda/envs/mhl_py311/lib/python3.11/site-packages/xgboost/core.py:726: FutureWarning: Pass `evals` as keyword args.
  warnings.warn(msg, FutureWarning)


[0]	train-auc:0.72404	eval-auc:0.59755
[1]	train-auc:0.77449	eval-auc:0.61684
[2]	train-auc:0.80143	eval-auc:0.61842
[3]	train-auc:0.82563	eval-auc:0.62081
[4]	train-auc:0.83993	eval-auc:0.62739
[5]	train-auc:0.85611	eval-auc:0.63009
[6]	train-auc:0.86313	eval-auc:0.63397
[7]	train-auc:0.87409	eval-auc:0.63416
[8]	train-auc:0.88935	eval-auc:0.63792
[9]	train-auc:0.89944	eval-auc:0.63648
[10]	train-auc:0.90767	eval-auc:0.63826
[11]	train-auc:0.91626	eval-auc:0.63678
[12]	train-auc:0.92196	eval-auc:0.63293
[13]	train-auc:0.92891	eval-auc:0.63344
[14]	train-auc:0.93481	eval-auc:0.63360
[15]	train-auc:0.93753	eval-auc:0.63349
[16]	train-auc:0.94254	eval-auc:0.63322
[17]	train-auc:0.94739	eval-auc:0.63347
[18]	train-auc:0.94938	eval-auc:0.63573
[19]	train-auc:0.95371	eval-auc:0.63360
[20]	train-auc:0.95596	eval-auc:0.63550


In [ ]:
# W/O Pressing Intensity
# Get predictions on the test set
y_pred = bst.predict(dtest)
y_pred_label = (y_pred > 0.5).astype(int)

# Calculate and print evaluation metrics
accuracy = accuracy_score(y_val, y_pred_label)
auc = roc_auc_score(y_val, y_pred)

print("Test Accuracy: {:.4f}".format(accuracy))
print("Test AUC: {:.4f}".format(auc))

Test Accuracy: 0.8027
Test AUC: 0.6491


: 

In [11]:
# W/O Pressing Intensity
# Get predictions on the test set
y_pred = bst.predict(dtest)
y_pred_label = (y_pred > 0.5).astype(int)

# Calculate and print evaluation metrics
accuracy = accuracy_score(y_val, y_pred_label)
auc = roc_auc_score(y_val, y_pred)

print("Test Accuracy: {:.4f}".format(accuracy))
print("Test AUC: {:.4f}".format(auc))

Test Accuracy: 0.7989
Test AUC: 0.6465


# 2. SoccerMap / exPress Evaluation

In [39]:
import torch
import pytorch_lightning as pl
from torch.utils.data import DataLoader
import json
import os
os.chdir('/home/work/MHL/express-v2')
import argparse # To accept checkpoint path as argument

# Import project modules
# import config  # Import static configurations
from model import PytorchSoccerMapModel # Import Lightning model
from datasets import PressingSequenceDataset, SoccerMapInputDataset 


In [40]:
pl.seed_everything(42, workers=True) # Ensure reproducibility

DATA_PATH = "/data/MHL/pressing-intensity" # Path where pickled datasets are saved
test_dataset = SoccerMapInputDataset(os.path.join(DATA_PATH, "test_dataset.pkl"))

if len(test_dataset) == 0:
    print("Loaded test dataset is empty. Exiting.")

# Custom collate function to handle potential None values from dataset errors
def collate_fn_skip_none(batch):
    batch = list(filter(lambda x: x is not None, batch))
    if not batch: return None
    try: return torch.utils.data.dataloader.default_collate(batch)
    except RuntimeError: return None # Skip batch if collation error

test_loader = DataLoader(
    test_dataset,
    batch_size=1,
    shuffle=False,
    num_workers=4,
    pin_memory=True,
    persistent_workers=True,
    # collate_fn=collate_fn_skip_none
)

Seed set to 42


Loading dataset from /data/MHL/pressing-intensity/test_dataset.pkl...


In [41]:
import argparse

parser = argparse.ArgumentParser(description="Train a pressing evaluation model.")
# parser.add_argument("--model_type", type=str, default="soccermap", choices=['soccermap', 'xgboost', 'exPress'], help="Path to the model checkpoint (.ckpt) file saved during training.")
# parser.add_argument("--root_path", type=str, default="/data/MHL/pressing-intensity", help="Path to the data file.")
parser.add_argument("--model_type", type=str, default="soccermap", choices=['soccermap', 'xgboost', 'exPress'], help="Path to the model checkpoint (.ckpt) file saved during training.")
parser.add_argument("--root_path", type=str, default="/data/MHL/pressing-intensity", help="Path to the data file.")
parser.add_argument("--mode", type=str, default="train", choices=['train', 'test'], help="Mode: 'train' or 'test'.")
parser.add_argument("--ckpt_path", type=str, default=None, help="Path to checkpoint file (Required for 'test' mode).")
parser.add_argument("--params_path", type=str, default="params.json", help="Path to the JSON containing configurations.")
parser.add_argument("--seed", type=int, default=42, help="Seed number.")

args = parser.parse_args([])

args.mode = 'test'
args.model_type = "exPress"
args.ckpt_path = "/data/MHL/pressing-intensity/checkpoints/exPress-epoch=28-val_loss=0.49.ckpt"

In [42]:
from components import press


component_dict = {
                    "soccermap": press.SoccerMapComponent,
                    "exPress": press.exPressComponent,
                }

exp = component_dict[args.model_type](args)

Seed set to 42


Configurations loaded from params.json.
